# Deliverable 3. Create a Travel Itinerary Map

----

1. Create a folder called `Vacation_Itinerary` to store all the files for this deliverable.

2. Download the `Vacation_Itinerary_starter_code.ipynb` file into your `Vacation_Itinerary` folder and rename it `Vacation_Itinerary.ipynb`.

3. Make sure the initial dependencies and the Geoapify API key are imported.

4. From your `Vacation_Search` folder from Deliverable 2, import the `WeatherPy_vacation.csv` file as a DataFrame named `vacation_df`.

5. Use GeoViews to create a map that shows all the cities in the `vacation_df` DataFrame. Configure the map as follows:

    * The point's size should be the maximum temperature for the city

    * The point's color should be the city's name

    * Use the `hover_cols` parameter to the the "Hotel Name", "Country", and "Current Description" columns to each point as additional information.

6. From the map, *choose four cities* that a customer might want to visit. They should be close together and in the same country. Use the `loc` method to create separate DataFrames for each city on the travel route.

    > **Hint:** You will start and end the route in the same city, so the `vacation_start` and `vacation_end` DataFrames will be in the same city.

7. Use the Pandas `concat` function to merge the DataFrame from each city in the itinerary to create a new DataFrame named `itinerary_df` to store the itinerary details.

8. Use the Pandas `copy` function to create a new DataFrame named `waypoints_df` to store the longitude and latitude for each city in `itinerary_df`.

    > **Hint:** You'll use this DataFrame to create a map using GeoViews, so recall that the first column should be the longitude, and the second the latitude.

9. Use GeoViews to create a map that shows the four cities in the itinerary.

10. Next, you'll use the Geoapify Routing API to find a route between the cities in the itinerary. Review the code that sets the initial parameters and fetches the coordinates from each city to define the `waypoints` parameter by using a `for` loop.

    > **Hint:** You can note that the `mode` parameter is set to `drive`, you can play around with other modes as it's shown in [the "Travel modes" table](https://apidocs.geoapify.com/docs/routing/#api) in the Geoapify Routing API documentation.

11. Use the Geoapify Routing API to retrieve the route's directions for your itinerary.

12. From the JSON response, store the route's legs coordinates in a variable called `legs`.

13. Loop through the route legs coordinates to fetch the latitude and longitude for each step. Store the latitude and longitude values into two Python lists named `longitude` and `latitude`.

14. Use the `longitude` and `latitude` Python lists to create a new DataFrame named `route_df`.

15. Use the GeoViews `Path` function to configure a line plot by using `route_df`. Set a custom color and width for the line that may contrast with the map.

16. Use the asterisk operator to display a composed plot that shows the itinerary's route over the map containing the cities. 

17. Save your map to the `Vacation_Itinerary` folder as `WeatherPy_travel_map.png`.

---

## Make sure the initial dependencies and the Geoapify API key are imported

In [8]:
# Dependencies and Setup
import geoviews as gv
import hvplot.pandas
import pandas as pd
import requests

# Turn off warning messages
import warnings
warnings.filterwarnings("ignore")

# Import API key
from config import geoapify_key

## From your `Vacation_Search` folder from Deliverable 2, import the `WeatherPy_vacation.csv` file as a DataFrame named `vacation_df`

In [9]:
# Read the WeatherPy_vacation.csv into a DataFrame
vacation_df = pd.read_csv("/Users/arashyousefi/Desktop/Analysis Project/Module-6/Vacation_Search/WeatherPy_vacation.csv") # YOUR CODE HERE

# Display sample data
# YOUR CODE HERE
vacation_df

Unnamed: 0           City Country  Max Temp weather_description      Lat  \
0             2           Hilo      US     82.13    scattered clouds  19.7297   
1             7         Atuona      PF     78.69     overcast clouds  -9.8000   
2            12      Cape Town      ZA     75.90           clear sky -33.9258   
3            19  Alice Springs      AU     88.21           clear sky -23.7000   
4            35          Kapaa      US     81.48    scattered clouds  22.0752   
..          ...            ...     ...       ...                 ...      ...   
105         607      Gorontalo      ID     76.64       broken clouds   0.5412   
106         613        Mandera      KE     77.45     overcast clouds   3.9366   
107         615        Atambua      ID     76.78     overcast clouds  -9.1061   
108         630          Kimbe      PG     78.03     overcast clouds  -5.5502   
109         656         Cosala      MX     79.41           clear sky  24.4125   

          Lng                 Hotel Name  
0   -155.0900          Dolphin Bay Hotel  
1   -139.0333               Pearl Resort  
2     18.4232            Townhouse Hotel  
3    133.8833       Aurora Alice Springs  
4   -159.3190            Pono Kai Resort  
..        ...                        ...  
105  123.0595           Grand City Hotel  
106   41.8670  Kornesh Hotel and Lodging  
107  124.8925             Hotel Matahari  
108  150.1429            Kimbe Bay Hotel  
109 -106.6908        Hotel Quinta Minera  

[110 rows x 8 columns]

## Use GeoViews to create a map that shows all the cities in the `vacation_df` DataFrame. Configure the map as follows:

* The point's size should be the maximum temperature for the city

* The point's color should be the city's name

* Use the `hover_cols` parameter to the the "Hotel Name", "Country", and "Current Description" columns to each point as additional information.

In [13]:
# Configure the map plot
map_plot =  vacation_df.hvplot.points(
    "Lng",
    "Lat",
    geo = True,
    tiles = "OSM",
    frame_width = 700,
    frame_height = 500,
    size = "Max Temp",
    scale = 1,
    color = "City",
    hover_cols = ["Hotel Name", "Country","weather_description"]# YOUR CODE HERE
)
# Display the map
map_plot  
# YOUR CODE HERE

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [Lng,Lat]   (City,Max Temp,Hotel Name,Country,weather_description)

## From the map, *choose four cities* that a customer might want to visit. They should be close together and in the same country. Use the `loc` method to create separate DataFrames for each city on the travel route.

In [41]:
# Create DataFrames for each city by filtering the 'vacation_df' using the loc method

vacation_start = "Tual"
vacation_end = "Tual"
city2 = "Barabai"
city3 = "Waingapu"
city4 = "Padang" 

vacation_start = vacation_df.loc[vacation_df["City"] == vacation_start]
vacation_end = vacation_df.loc[vacation_df["City"] == vacation_end]  
vacation_stop2 = vacation_df.loc[vacation_df["City"] == city2]
vacation_stop3 = vacation_df.loc[vacation_df["City"] == city3] 
vacation_stop4 = vacation_df.loc[vacation_df["City"] == city4]   

## Use the Pandas `concat` function to merge the DataFrame from each city in the itinerary to create a new DataFrame named `itinerary_df` to store the itinerary details

In [42]:
# Use the Pandas concat function to create a new DataFrame to store the itinerary details.

itinerary_df = pd.concat([vacation_start, vacation_stop2, vacation_stop3, vacation_stop4, vacation_end],ignore_index=True)

# Display sample data
itinerary_df
# YOUR CODE HERE

Unnamed: 0      City Country  Max Temp weather_description     Lat  \
0         338      Tual      ID     83.21     overcast clouds -5.6667   
1         340   Barabai      ID     75.00     overcast clouds -2.5833   
2         397  Waingapu      ID     79.79     overcast clouds -9.6567   
3         441    Padang      ID     75.52     overcast clouds -0.9492   
4         338      Tual      ID     83.21     overcast clouds -5.6667   

        Lng        Hotel Name  
0  132.7500             Suita  
1  115.3833      Hotel Bouraq  
2  120.2641  HOTEL SANDLEWOOD  
3  100.3543      losmen Surya  
4  132.7500             Suita

## Use the Pandas `copy` function to create a new DataFrame named `waypoints_df` to store the longitude and latitude for each city in `itinerary_df`

In [50]:
# Create a Pandas DataFrame to store the latitude and longitude for each city in the itineray

waypoints_df = itinerary_df[["Lat", "Lng"]]

    # YOUR CODE HERE


# Display sample data
waypoints_df
# YOUR CODE HERE

Lat       Lng
0 -5.6667  132.7500
1 -2.5833  115.3833
2 -9.6567  120.2641
3 -0.9492  100.3543
4 -5.6667  132.7500

## Use GeoViews to create map that shows the four cities in the itinerary

In [51]:


# Configure the map plot
# YOUR CODE HERE
waypoints_map = itinerary_df.hvplot.points(
    "Lng",
    "Lat",
    geo = True,
    tiles = "OSM",
    frame_width = 700,
    frame_height = 500,
    size = "Max Temp",
    scale = 1,
    color = "City",
    hover_cols = ["City", "Country","weather_description"]
)
# Display the map
# YOUR CODE HERE
waypoints_map
# YOUR CODE HERE

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [Lng,Lat]   (City,Max Temp,Country,weather_description)

## Next, you'll use the Geoapify Routing API to find a route between the cities in the itinerary. Review the code that sets the initial parameters and fetches the coordinates from each city to define the `waypoints` parameter by using a `for` loop

In [55]:
# Set parameters to trace the route
radius = 5000
params = {
    "mode":"drive",
    "apiKey": geoapify_key,
}

In [59]:
# Set an empty waypoints String variable
waypoints = ""

# Iterate through the route_df DataFrame to define the waypoints
for index, row in waypoints_df.iterrows():
    waypoints = waypoints + str(row["Lat"]) + "," + str(row["Lng"]) + "|"

# Delete the last character from the string
waypoints = waypoints[:-1]

# Add the waypoints to the params dictionary
params["waypoints"] = waypoints

# Display the params dictionary
params

{'mode': 'drive',
 'apiKey': 'ed4e1e0529c84cc3b950529cb6099f10',
 'waypoints': '-5.6667,132.75|-2.5833,115.3833|-9.6567,120.2641|-0.9492,100.3543|-5.6667,132.75'}

## Use the Geoapify Routing API to retrieve the route's directions for your itinerary

In [60]:
# Set up the base URL for the Geoapify Places API.
base_url = "https://api.geoapify.com/v1/routing"

# Make request and retrieve the JSON data by using the params dictionaty
route_response = requests.get(base_url , params=params )# YOUR CODE HERE

# Convert the API response to JSON format
route_response = route_response.json() # YOUR CODE HERE
route_response

{'features': [{'type': 'Feature',
   'properties': {'mode': 'drive',
    'waypoints': [{'location': [132.75, -5.6667], 'original_index': 0},
     {'location': [115.3833, -2.5833], 'original_index': 1},
     {'location': [120.2641, -9.6567], 'original_index': 2},
     {'location': [100.3543, -0.9492], 'original_index': 3},
     {'location': [132.75, -5.6667], 'original_index': 4}],
    'units': 'metric',
    'distance': 13114634,
    'distance_units': 'meters',
    'time': 933955.265,
    'legs': [{'distance': 2989797,
      'time': 258666,
      'steps': [{'from_index': 0,
        'to_index': 4,
        'distance': 160,
        'time': 16.457,
        'instruction': {'text': 'Drive west.'}},
       {'from_index': 4,
        'to_index': 26,
        'distance': 336,
        'time': 36.202,
        'instruction': {'text': 'Turn left.'}},
       {'from_index': 26,
        'to_index': 87,
        'distance': 2682,
        'time': 209.38,
        'instruction': {'text': 'Turn right.'}},
    

## From the JSON response, store the route's legs coordinates in a variable called `legs`

In [61]:
# Fetch the route's legs coordinates from the JSON reponse
legs =  route_response["features"][0]["geometry"]["coordinates"] # YOUR CODE HERE

## Loop through the route legs coordinates to fetch the latitude and longitude for each step. Store the latitude and longitude value into two Python lists names `longitude` and `latitude`

In [62]:
# Create and empty list to store the longitude of each step
# YOUR CODE HERE
Longitude = []
# Create and empty list to store the latitude of step
# YOUR CODE HERE
Latitude = []

# Loop through the legs coordinates to fetch the latitude and longitude for each step
# YOUR CODE HERE
for leg in legs:
    for coordinate in leg:
        Longitude.append(coordinate[0])
        Latitude.append(coordinate[1])

## Use the `longitude` and `latitude` Python lists to create a new DataFrame named `route_df`

In [65]:
# Create an empty DataFrame to store the steps' coordinates
route_df = pd.DataFrame()

# Add the steps' longitude and latitude from each step as columns to the DataFrame
# YOUR CODE HERE
route_df["Longitude"] = Longitude

route_df["Latidude"] = Latitude
# Display sample data
# YOUR CODE HERE
route_df.head()

Longitude  Latidude
0  132.750401 -5.660880
1  132.750191 -5.660814
2  132.749782 -5.660589
3  132.749424 -5.660457
4  132.749081 -5.660312

##  Use the GeoViews `Path` function to configure a line plot by using `route_df`. Set a custom color and width for the line that may contrast with the map

In [74]:
# Configure the route path by using the GeoViews' Path function
route_path = gv.Path(
    route_df,
).opts(
                 height = 600,
                 width = 800,
                 line_width = 5,
                 color = "green"
)# YOUR CODE HERE


In [77]:
# Display a composed plot by using the route_map and route_path objects


waypoints_map * route_path
# YOUR CODE HERE

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [Lng,Lat]   (City,Max Temp,Country,weather_description)
   .Path.I   :Path   [Longitude,Latidude]